# TWL Exceedance

## Setup notebook

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
from tqdm import tqdm_notebook
from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML
from scipy import stats
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from scipy.interpolate import interp1d

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,6)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"


# https://stackoverflow.com/a/20709149
matplotlib.rcParams['text.usetex'] = True
matplotlib.rcParams['font.family'] = 'sans-serif'
matplotlib.rcParams['font.sans-serif'] = 'Helvetica'

matplotlib.rcParams['text.latex.preamble'] = [
       r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
       r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
       r'\usepackage{helvet}',    # set the normal font here
       r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
       r'\sansmath'               # <- tricky! -- gotta actually tell tex to use!
]  

## Import data

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}
print('Done!')

## Calculate impact hours
- For each site_id, determine the R2 elevation.

In [ ]:
# Create figure to plot results
fig = tools.make_subplots(
    rows=2,
    cols=2,
    specs=[[{}, {}], [{}, {}]],
    subplot_titles=('Swash/Swash', 'Swash/Collision', 'Collision/Swash',
                    'Collision/Collision'),
    shared_xaxes=True,
    shared_yaxes=True,
    horizontal_spacing=0.05,
    vertical_spacing=0.1,
    print_grid=False)

# Iterate through each site
print('Calculating cumulate frequency of R_high for each site:')
site_ids = twls['forecasted']['mean_slope_sto06'].index.get_level_values(
    'site_id').unique().values
for site_id in tqdm_notebook(site_ids):

    # Put data into a temporary dataframe, shorter name is easier to work with
    df_impacts = impacts['forecasted']['mean_slope_sto06'].loc[site_id]
    df_twls = twls['forecasted']['mean_slope_sto06'].loc[site_id]

    D_low = df_impacts.dune_toe_z
    if np.isnan(D_low):
        continue

    # Get R_high elevations minus dune toe
    R_high_ts = df_twls.R_high.dropna().values
    R_high_D_low_ts = R_high_ts - D_low

    # Get SWL minus dune toe
    SWL_D_low_ts = df_twls['tide'].dropna().values - D_low
    DSWL_D_low_ts = (df_twls['tide'] + df_twls['setup']).dropna().values - D_low

    # Get cumulative freq
    cumfreq = stats.cumfreq(R_high_D_low_ts, numbins=100)
#     cumfreq = stats.cumfreq(DSWL_D_low_ts, numbins=100)

    # Calculate space of values for x
    bin_vals = cumfreq.lowerlimit + np.linspace(
        0, cumfreq.binsize * cumfreq.cumcount.size, cumfreq.cumcount.size)

    # Check which subplot we should put this site on
    forecasted_regime = impacts['forecasted']['mean_slope_sto06'].loc[
        site_id].storm_regime
    observed_regime = impacts['observed'].loc[site_id].storm_regime

    if forecasted_regime == 'swash' and observed_regime == 'swash':
        x_col = 1
        y_col = 1
    elif forecasted_regime == 'collision' and observed_regime == 'collision':
        x_col = 2
        y_col = 2
    elif forecasted_regime == 'swash' and observed_regime == 'collision':
        x_col = 2
        y_col = 1
    elif forecasted_regime == 'collision' and observed_regime == 'swash':
        x_col = 1
        y_col = 2
    else:
        continue

    fig.append_trace(
        go.Scattergl(
            x=bin_vals,
            y=[max(cumfreq.cumcount) - x for x in cumfreq.cumcount],
            name=site_id,
            line=dict(
                color=('rgba(22, 22, 22, 0.2)'),
                width=0.5,
            )), x_col, y_col)

print('Finalizing plot:')
# Change some formatting for the plot
layout = go.Layout(
    xaxis=dict(domain=[0, 0.45]),
    yaxis=dict(
        domain=[0, 0.45],
        type='log',
    ),
    xaxis2=dict(domain=[0.55, 1]),
    xaxis4=dict(domain=[0.55, 1], anchor='y4'),
    yaxis3=dict(
        domain=[0.55, 1],
        type='log',
    ),
    yaxis4=dict(
        domain=[0.55, 1],
        anchor='x4',
        type='log',
    ))

fig['layout'].update(
    showlegend=False,
    title='Impact hours',
    height=800,
)

for ax in ['yaxis', 'yaxis2']:
#     fig['layout'][ax]['range'] = [0, 400]
    fig['layout'][ax]['range'] = [0, 15]

for ax in ['xaxis', 'xaxis2']:
#     fig['layout'][ax]['range'] = [-2.5, 2.5]
    fig['layout'][ax]['range'] = [-1, 1]

fig['layout']['xaxis'].update(title='R_high - D_low')
fig['layout']['xaxis2'].update(title='R_high - D_low')
fig['layout']['yaxis'].update(title='No. of Hours')
fig['layout']['yaxis2'].update(title='No. of Hours')

# pio.write_image(fig, 'fig2.png')

go.FigureWidget(fig)

This gives an overview of the distribution of impact hours. Try to calculate the confidence interval bounds for each prediction/observed combination.

The following cell looks at combining all the observations from each CDF into one large CDF and calculating a confidence interval from it, but I'm not sure if this is a valid method.

In [ ]:
from statsmodels.distributions.empirical_distribution import ECDF
from statsmodels.distributions.empirical_distribution import _conf_set

df_twls = twls['forecasted']['mean_slope_sto06']
df_forecasted_impacts = impacts['forecasted']['mean_slope_sto06']
df_observed_impacts = impacts['observed']

plt.figure(figsize=(6,8))

# Do some data rearranging and joining to make it easier
df_joined = df_twls.reset_index()
df_joined = df_joined.set_index('site_id')
df_joined = df_joined.merge(
    df_observed_impacts[['storm_regime']],
    left_on='site_id',
    right_on='site_id').rename({
        'storm_regime': 'observed_regime'
    },
                               axis='columns')
df_joined = df_joined.merge(
    df_forecasted_impacts[['storm_regime', 'dune_toe_z']],
    left_on='site_id',
    right_on='site_id').rename({
        'storm_regime': 'forecasted_regime'
    },
                               axis='columns')

regime_combinations = [
    ('swash', 'swash', '#2b83ba'),
    ('collision', 'swash', '#abdda4'),
    ('swash', 'collision', '#fdae61'),
    ('collision', 'collision', '#d7191c'),
]

for comb in regime_combinations:

    observed_regime = comb[0]
    forecasted_regime = comb[1]
    color = comb[2]

    # Get values of elevation difference to plot
    query = '(observed_regime=="{}") & (forecasted_regime=="{}")'.format(
        observed_regime, forecasted_regime)
    df = df_joined.query(query)
    R_high_D_low = (df.R_high - df.dune_toe_z).values
    R_high_D_low = R_high_D_low[~np.isnan(R_high_D_low)]

    ecdf = ECDF(R_high_D_low)

    y = ecdf.y
    lower, upper = _conf_set(y, alpha=0.05)
    x = ecdf.x

    avg_hrs = df.groupby('site_id').count().R_high.mean()
    y = [avg_hrs - v * avg_hrs for v in y]
    lower = [avg_hrs - v * avg_hrs for v in lower]
    upper = [avg_hrs - v * avg_hrs for v in upper]

    plt.step(
        x,
        y,
        color=color,
        label='Pred={}, Obs={}'.format(forecasted_regime, observed_regime))
    plt.fill_between(
        x, y, upper, color='grey', alpha=0.2, interpolate=False, step='pre')
    plt.fill_between(
        x, y, lower, color='grey', alpha=0.2, interpolate=False, step='pre')

# # Plot for checking

plt.title('Empirical CDF with 95\% confidence intervals')
plt.xlabel('$R_{high} - D_{low} (m)$')
plt.ylabel('Hours of Elevation Exceedence')
plt.xlim([-1, 1])
plt.ylim([0, 25])
plt.legend(loc='best')

# Print to figure
plt.savefig('05-empirical-cdf.png', dpi=600, bbox_inches='tight') 
plt.show()

The plot above shows:
- collision if R_high - D_low > 0.25 m for 6 hours
- swash if R_high - D_low < -0.8m for 7 hours

additionaly:
- collision if R_high > D_low for more than 10 hours
    
Let's test how these new critera would perform.

In [ ]:
# Calculate elevation exceedence for each hours we are interested in
ele_exceedence_6hr = twls['forecasted']['mean_slope_sto06'].sort_values(['R_high'],ascending=False).groupby('site_id').R_high.nth(6-1).rename('ele_exceedence_6hr')

ele_exceedence_7hr = twls['forecasted']['mean_slope_sto06'].sort_values(['R_high'],ascending=False).groupby('site_id').R_high.nth(7-1).rename('ele_exceedence_7hr')


ele_exceedence_2hr = twls['forecasted']['mean_slope_sto06'].sort_values(['R_high'],ascending=False).groupby('site_id').R_high.nth(2-1).rename('ele_exceedence_2hr')

ele_exceedence_1hr = twls['forecasted']['mean_slope_sto06'].sort_values(['R_high'],ascending=False).groupby('site_id').R_high.nth(0).rename('ele_exceedence_1hr')


# Get our dune toes
dune_toes = df_profile_features_crest_toes.xs('prestorm',level='profile_type')['dune_toe_z']

# Get our observed regimes
observed_regime = impacts['observed'].storm_regime.rename('observed_regime')

# Concat into one data frame
df = pd.concat([dune_toes, ele_exceedence_6hr, ele_exceedence_7hr, ele_exceedence_1hr, ele_exceedence_2hr, observed_regime],axis=1)

# Get predicted regime based on old criteria
df.loc[df.ele_exceedence_1hr < df.dune_toe_z, 'forecasted_regime'] = 'swash'
df.loc[df.ele_exceedence_1hr > df.dune_toe_z , 'forecasted_regime'] = 'collision'


regime_combinations = [
    ('swash','swash'),
    ('collision','swash'),
    ('swash','collision'),
    ('collision','collision'),
]

print('Original')
for comb in regime_combinations:
    query = 'forecasted_regime=="{}" & observed_regime=="{}"'.format(comb[0], comb[1])
    print('Forecasted: {}, Observed: {}, Count: {}'.format(comb[0], comb[1], len(df.query(query))))


# Get predicted regime based on our new criteria

adjust_swash_criteria = (df.forecasted_regime == 'swash') & (df.ele_exceedence_7hr - df.dune_toe_z > -0.8)
adjust_collision_criteria = (df.forecasted_regime == 'collision') & (df.ele_exceedence_6hr - df.dune_toe_z < 0.25)
df.loc[adjust_swash_criteria, 'forecasted_regime'] = 'collision'
df.loc[adjust_collision_criteria, 'forecasted_regime'] = 'swash'

# df.loc[(df.ele_exceedence_1hr - df.dune_toe_z <= -0.15  ),'forecasted_regime'] = 'swash'
# df.loc[(df.ele_exceedence_1hr - df.dune_toe_z > -0.15  ),'forecasted_regime'] = 'collision'


print('\nAfter adjustment')
for comb in regime_combinations:
    query = 'forecasted_regime=="{}" & observed_regime=="{}"'.format(comb[0], comb[1])
    print('Forecasted: {}, Observed: {}, Count: {}'.format(comb[0], comb[1], len(df.query(query))))


Looking at the adjusted values, we can see these criteria actually make it worse. There must be something wrong with the technique - maybe the way of calculating the confidence intervals is wrong? Let's try calculate confidence intervals for each regime combination.

*This cell I don't think is used...*


In [ ]:
def mean_confidence_interval(data, confidence=0.95):
    a = 1.0 * np.array(data)
    n = len(a)
    m, se = np.mean(a), stats.sem(a)
    h = se * stats.t.ppf((1 + confidence) / 2., n-1)
    return m, m-h, m+h

# Add columns indicating how many n hrs was this the largest record
df = twls['forecasted']['mean_slope_sto06'].sort_values(['R_high'],ascending=False)
df['n_hrs_largest']= df.groupby('site_id').cumcount()+1

# Join observed and forecast impacts and dune toe elevation
observed_regime = impacts['observed'].storm_regime.rename('observed_regime').to_frame()
forecasted_regime = impacts['forecasted']['mean_slope_sto06'].storm_regime.rename('forecasted_regime').to_frame()
dune_info = df_profile_features_crest_toes.xs('prestorm', level='profile_type')

df['datetime'] = df.index.get_level_values('datetime')
df = df.merge(observed_regime,left_on=['site_id'],right_on='site_id')
df = df.merge(forecasted_regime,left_on=['site_id'],right_on='site_id')
df = df.merge(dune_info,left_on=['site_id'],right_on='site_id')

# Make new column for R_high minus D_low
df['R_high_D_low_diff'] = df.R_high - df.dune_toe_z


regime_combinations = [
    ('swash','swash'),
    ('swash','collision'),
    ('collision','swash'),
    ('collision','collision'),
]

print('Calculating hr exceedence elevations for each combination:')
exceedence_data = []
for hr in tqdm_notebook([x for x in range(1,101)]):
    
    for comb in regime_combinations:
        
        vals = df.loc[(df.n_hrs_largest==hr) & (df.observed_regime==comb[0]) & (df.forecasted_regime==comb[1])].R_high_D_low_diff.dropna().values
    
        ci = mean_confidence_interval(vals)

        exceedence_data.append({
            'observed_regime': comb[0],
            'forecasted_regime': comb[1],
            'exceedence_hr': hr,
            'ci_mean': ci[0],
            'ci_lower': ci[1],
            'ci_upper': ci[2],
        })
        
  

Let's try a different apporach and try split the observed swash and collision regimes at each impact duration hour. 

In [ ]:
from scipy.stats import norm

best_split = []
exceedence_hrs = []
swash_mean = []
swash_95_lower = []
swash_95_upper = []
collision_mean = []
collision_95_lower = []
collision_95_upper = []
swash_median = []
swash_q1 = []
swash_q3 = []
collision_median = []
collision_q1 = []
collision_q3 = []

for hr in tqdm_notebook([x for x in range(1,101)]):
    
    dists = []
    plt.figure(figsize=(10,2))
    for observed_regime in ['swash','collision']:
        
        vals = df.loc[(df.n_hrs_largest==hr) &
                      (df.observed_regime==observed_regime)].R_high_D_low_diff.dropna().values
      
        if observed_regime =='collision':
            color = 'red'
            label='collision'
        else:
            color = 'blue'
            label='swash'
            
        plt.hist(vals, bins='auto',color=color, alpha=0.5,label=label)  
        plt.title("{} hour exceedence TWL".format(hr))
        plt.xlim([-2.5,2.5])
        
        dists.append(norm.fit(vals))
  
    # Find which elevation best splits swash and collision
#     eles = [x for x in np.linspace(-2,2,1000)]
#     total_cdfs = []
#     for ele in eles:
#         swash_cdf = norm.cdf(ele,*dists[0])
#         collision_cdf = 1 - norm.cdf(ele,*dists[1])
#         total_cdfs.append(swash_cdf + collision_cdf)

#     i_max = np.argmax(total_cdfs)
#     best_ele = eles[i_max]

#     exceedence_hrs.append(hr)
#     best_split.append(best_ele)

    # Find which elevation best splits swash and collision
    eles = [x for x in np.linspace(-2,2,100)]
    total_cdfs = []
    swash_vals = df.loc[(df.n_hrs_largest==hr) &
                  (df.observed_regime=='swash')].R_high_D_low_diff.dropna().values
    collision_vals = df.loc[(df.n_hrs_largest==hr) &
                  (df.observed_regime=='collision')].R_high_D_low_diff.dropna().values
    for ele in eles:
        swash_samples = np.sum( swash_vals < ele) / len(swash_vals)
        collision_samples = np.sum( collision_vals > ele) / len(collision_vals)        
        total_cdfs.append(swash_samples + collision_samples)
    
    i_max = np.argmax(total_cdfs)
    best_ele = eles[i_max]

    exceedence_hrs.append(hr)
    best_split.append(best_ele)    
    
    
    # Store stastistics
    swash_mean.append(dists[0][0])
    swash_95_lower.append(norm.interval(0.5, *dists[0])[0])
    swash_95_upper.append(norm.interval(0.5, *dists[0])[1])
    collision_mean.append(dists[1][0])
    collision_95_lower.append(norm.interval(0.5, *dists[1])[0])
    collision_95_upper.append(norm.interval(0.5, *dists[1])[1])
    
    swash_median.append(np.percentile(swash_vals, 50))
    swash_q1.append(np.percentile(swash_vals, 25))
    swash_q3.append(np.percentile(swash_vals, 75))
    collision_median.append(np.percentile(collision_vals, 50))
    collision_q1.append(np.percentile(collision_vals, 25))
    collision_q3.append(np.percentile(collision_vals, 75))    
    
    plt.axvline(best_ele, label='Best split (x={:.2f} m)'.format(best_ele))
    plt.legend(loc='upper right', prop={'size': 10} )
    plt.xlabel('$R_{high} - D_{low}$')
    plt.ylabel('No. of sites')
    plt.xlim([-2,2])
    if hr == 80 or hr < 5 or hr==90:
        plt.show()
        
    plt.close()

Now, let's plot our distributions for swash/collision and the best seperation between them.

In [ ]:
plt.figure(figsize=(5,5))
plt.plot(best_split,exceedence_hrs, label='Best split', color='#000000', linestyle='--')

# plt.plot(swash_mean, exceedence_hrs, label='Swash', color='#2b83ba')
# plt.fill_betweenx(exceedence_hrs,swash_95_lower,swash_95_upper, color='#2b83ba', alpha=0.2, interpolate=False)

# plt.plot(collision_mean, exceedence_hrs, label='Collision', color='#d7191c')
# plt.fill_betweenx(exceedence_hrs,collision_95_lower,collision_95_upper, color='#d7191c', alpha=0.2, interpolate=False,label='plus 50')


plt.plot(swash_median, exceedence_hrs, label='Swash', color='#2b83ba')
plt.fill_betweenx(exceedence_hrs,swash_q1,swash_q3, color='#2b83ba', alpha=0.2, interpolate=False,label='Swash IQR')

plt.plot(collision_median, exceedence_hrs, label='Collision', color='#d7191c')
plt.fill_betweenx(exceedence_hrs,collision_q1,collision_q3, color='#d7191c', alpha=0.2, interpolate=False,label='Collision IQR')





#===
# # Let's plot one site as well, just to check
# import random
# site_ids = list(impacts['observed'].index.unique().values)
# site_id = random.choice(site_ids)


# site_id = 'TREACH0011'
# site_predicted_regime = impacts['forecasted']['mean_slope_sto06'].loc[site_id].storm_regime
# site_observed_regime = impacts['observed'].loc[site_id].storm_regime
# df_site = df.loc[site_id]
# plt.plot(df_site.R_high_D_low_diff, df_site.n_hrs_largest,label='site_id={}\n(pred={},obs={})'.format(site_id,site_predicted_regime, site_observed_regime),color='#ffffff', linestyle='--')


plt.title('Observed Swash/Collision - Best Split')
plt.xlabel('$R_{high} - D_{low}$ (m)')
plt.ylabel('Exceedance hours')
plt.ylim([0,100])
plt.xlim([-2,2])
plt.legend()

# Print to figure
plt.savefig('05-best-split.png', dpi=600, bbox_inches='tight') 

plt.show()
plt.close()

Plot above shows that if Rhigh = Dlow plus/minus 0.25m, we should say the storm regime is uncertain, rather than trying to make an incorrect prediction.

In [ ]:
df_for = impacts['forecasted']['mean_slope_sto06']
df_obs = impacts['observed']

# Join forecasted and observed impacts into same dataframe
df_for = df_for.rename(columns={'storm_regime': 'forecasted_regime'})
df_obs = df_obs.rename(columns={'storm_regime': 'observed_regime'})
df_for = df_for.merge(
    df_obs.observed_regime.to_frame(), left_index=True, right_index=True)

# Get wrong forecasts
incorrect_for = df_for.forecasted_regime != df_for.observed_regime

# How many wrong/correct forecasts
print('There were {} correct forecasts'.format(len(df_for[~incorrect_for])))
print('There were {} incorrect forecasts'.format(len(df_for[incorrect_for])))
print('')

# How many of these forecasts were where R_high was near D_low?
close_eles = ((df.R_high > df.dune_toe_z - 0.25) &
              (df.R_high < df.dune_toe_z + 0.25))

s = 'R_high and D_low elevations were close at {} correctly forecasted sites'
print(s.format(len(df_for[~incorrect_for & close_eles])))

s = 'R_high and D_low elevations were close at {} wrongly forecasted sites'
print(s.format(len(df_for[incorrect_for & close_eles])))

# df[(df.R_high>df.dune_toe_z-0.25)&(df.R_high<df.dune_toe_z+0.25)]

So we can see more than half the number of incorrect predictions by saying they're unknown, but a quarter of correct predictions will say they're unknown.

In [ ]:
# df_exceedence = pd.DataFrame(exceedence_data)
# df_exceedence = df_exceedence.set_index(['observed_regime','forecasted_regime','exceedence_hr'])

# import random
# site_ids = list(impacts['observed'].index.unique().values)
# for site_id in random.sample(site_ids, 5):

#     # Plot mean ele exceedence hours for each combination
#     plt.figure(figsize=(10,4))
#     regime_combinations = [
#         ('swash','swash'),
#         ('swash','collision'),
#         ('collision','swash'),
#         ('collision','collision'),
#     ]

#     for comb in regime_combinations:
#         df_plot = df_exceedence.xs((comb[0], comb[1]), level=['observed_regime','forecasted_regime'])
#         plt.plot(df_plot.ci_mean, df_plot.index.values,label='obs={}, pred={}'.format(comb[0],comb[1]))
#         plt.fill_betweenx(df_plot.index.values, df_plot.ci_lower, df_plot.ci_upper, color='grey', alpha=0.2, interpolate=False)

#     plt.xlim([-2,1])
#     plt.ylim([0,100])

#     # Let's plot one site as well, just to check
#     site_predicted_regime = impacts['forecasted']['mean_slope_sto06'].loc[site_id].storm_regime
#     site_observed_regime = impacts['observed'].loc[site_id].storm_regime
#     df_site = df.loc[site_id]
#     plt.plot(df_site.R_high_D_low_diff, df_site.n_hrs_largest,label='site_id={} (pred={},obs={})'.format(site_id,site_predicted_regime, site_observed_regime))

#     plt.legend(loc='upper right', prop={'size': 8})
#     plt.show()





# Other stuff which hasn't been tidied up

### Check the relationship between SWL-Dtoe, DSWL-Dtoe, R_high-Dtoe
Use 3D scatter plot to check the relationship between SWL-Dtoe, DSWL-Dtoe, R_high-Dtoe.

This is moving away from time dependence...

In [ ]:
[x[1] for x in df.query('forecasted_regime=="swash" & observed_regime=="swash"').iterrows()][0]

In [ ]:
data = []

# Iterate through each site
print('Calculating cumulate frequency of R_high for each site:')
site_ids = twls['forecasted']['mean_slope_sto06'].index.get_level_values(
    'site_id').unique().values
for site_id in tqdm_notebook(site_ids):

    # Put data into a temporary dataframe, shorter name is easier to work with
    df_impacts = impacts['forecasted']['mean_slope_sto06'].loc[site_id]
    df_twls = twls['forecasted']['mean_slope_sto06'].loc[site_id]

    D_low = df_impacts.dune_toe_z
    if np.isnan(D_low):
        continue

    # Find time where R_max is the highest
    t = df_twls.R_high.idxmax()

    # Get R_high, tide and setup at that time
    R_high = df_twls.loc[t].R_high
    tide = df_twls.loc[t].tide
    setup = df_twls.loc[t].setup

    # Calculate differences in elevation
    R_high_D_low = R_high - D_low
    SWL_D_low = tide - D_low
    DSWL_D_low = tide + setup - D_low

    # Check which subplot we should put this site on
    forecasted_regime = impacts['forecasted']['mean_slope_sto06'].loc[
        site_id].storm_regime
    observed_regime = impacts['observed'].loc[site_id].storm_regime

    data.append({
        'R_high_D_low': R_high_D_low,
        'SWL_D_low': SWL_D_low,
        'DSWL_D_low': DSWL_D_low,
        'forecasted_regime': forecasted_regime,
        'observed_regime': observed_regime
    })

# Turn data into a dataframe and plot
df = pd.DataFrame(data)

# Plot swash/swash
query='forecasted_regime=="swash" & observed_regime=="swash"'
trace1 = go.Scatter3d(
    x=[x[1].R_high_D_low for x in df.query(query).iterrows()],
    y=[x[1].SWL_D_low for x in df.query(query).iterrows()],
    z=[x[1].DSWL_D_low for x in df.query(query).iterrows()],
    name='Swash/Swash',
    mode='markers',
    marker=dict(
        size=6,
        color='rgb(26,150,65)',
        opacity=0.8))

query='forecasted_regime=="swash" & observed_regime=="collision"'
trace2 = go.Scatter3d(
    x=[x[1].R_high_D_low for x in df.query(query).iterrows()],
    y=[x[1].SWL_D_low for x in df.query(query).iterrows()],
    z=[x[1].DSWL_D_low for x in df.query(query).iterrows()],
    name='Swash/Collision',
    mode='markers',
    marker=dict(
        size=6,
        color='rgb(253,174,97)',
        opacity=0.8))

query='forecasted_regime=="collision" & observed_regime=="swash"'
trace3 = go.Scatter3d(
    x=[x[1].R_high_D_low for x in df.query(query).iterrows()],
    y=[x[1].SWL_D_low for x in df.query(query).iterrows()],
    z=[x[1].DSWL_D_low for x in df.query(query).iterrows()],
    name='Collision/Swash',
    mode='markers',
    marker=dict(
        size=6,
        color='rgb(166,217,106)',
        opacity=0.8))

query='forecasted_regime=="collision" & observed_regime=="collision"'
trace4 = go.Scatter3d(
    x=[x[1].R_high_D_low for x in df.query(query).iterrows()],
    y=[x[1].SWL_D_low for x in df.query(query).iterrows()],
    z=[x[1].DSWL_D_low for x in df.query(query).iterrows()],
    name='Collsion/Collision',
    mode='markers',
    marker=dict(
        size=6,
        color='rgb(215,25,28)',
        opacity=0.8))

layout = go.Layout(
    autosize=False,
    width=1000,
    height=700,
    margin=go.layout.Margin(
        l=50,
        r=50,
        b=100,
        t=100,
        pad=4
    ),
)

fig = go.Figure(data=[trace1,trace2,trace3,trace4], layout=layout)
go.FigureWidget(fig)


## Calculate vertical distribution of wave count SS
For each site, calculate how many waves reached a certain elevation (store as a binned histogram).

In [ ]:
# Helper functions
def find_nearest(array, value):
    array = np.asarray(array)
    idx = np.nanargmin((np.abs(array - value)))
    return array[idx], idx

In [ ]:
data = []
for site_id, df_site_twl in twls['forecasted']['mean_slope_sto06'].groupby('site_id'):
    
    twl_eles_per_wave = []
    
    # Iterate through each timestamp and calculate the number of waves at each interavl.
    # THIS LOOP IS SLOW
    for row in df_site_twl.itertuples():
        
        distribution = stats.norm(loc=row.tide+row.setup, scale=row.S_total/4) # CHECK

        # Total number of waves we expect in this period
        n_waves = int(3600 / row.Tp)  # Check that we have 1 hour
        
        # Get z elevation of each wave twl in this hour and append to list
        twl_eles_per_wave.extend([distribution.ppf(1-x/n_waves) for x in range(1,n_waves+1)])
    
    # Remove nans and infs # CHECK WHY INF
    twl_eles_per_wave = list(np.asarray(twl_eles_per_wave)[np.isfinite(twl_eles_per_wave)])
    
    # Sort wave twl z elevations in descending list
    twl_eles_per_wave.sort(reverse=True)    
    
    # Get index of closest value of dune toe. This is the number of waves that exceeded the the dune toe
    try:
        _, idx =  find_nearest(twl_eles_per_wave, dune_toe_z)
    except:
        continue
    
    # Get forecasted and observed impacts
    forecasted_regime = impacts['forecasted']['mean_slope_sto06'].loc[site_id,'storm_regime']
    observed_regime = impacts['observed'].loc[site_id,'storm_regime']
    
    counts, bin_edges = np.histogram(twl_eles_per_wave, bins=100) 
    
    data.append({
        'site_id': site_id,
        'forecasted_regime': forecasted_regime,
        'observed_regime': observed_regime,
        'n_waves_exceeding_dune_toe': idx,
        'n_waves': [x for x in range(0,500,1)],
        'truncated_twl_levels': [twl_eles_per_wave[x] for x in range(0,500,1)],
        'truncated_dune_toe_z': df_profile_features_crest_toes.loc[(site_id,'prestorm'),'dune_toe_z'],
        'full_counts': counts,
        'full_bin_edges': bin_edges,
    })
    
    print('Done {}'.format(site_id))

data_twl = data
# df = pd.DataFrame(data)
# df = df.set_index('site_id')

In [ ]:
fig = tools.make_subplots(
    rows=2,
    cols=2,
    specs=[[{}, {}], [{}, {}]],
    subplot_titles=('Swash/Swash',  'Swash/Collision', 
                    'Collision/Swash', 'Collision/Collision'),
 shared_xaxes=True, shared_yaxes=True,)

data = []
for site in data_twl:
    if site['forecasted_regime'] == 'swash' and site[
            'observed_regime'] == 'swash':
        x_col = 1
        y_col = 1
    elif site['forecasted_regime'] == 'collision' and site[
            'observed_regime'] == 'collision':
        x_col = 2
        y_col = 2
    elif site['forecasted_regime'] == 'swash' and site[
            'observed_regime'] == 'collision':
        x_col = 2
        y_col = 1
    elif site['forecasted_regime'] == 'collision' and site[
            'observed_regime'] == 'swash':
        x_col = 1
        y_col = 2
    else:
        continue

    fig.append_trace(
        go.Scattergl(
            x=[x - site['dune_toe_z'] for x in site['twl_levels']],
            y=site['n_waves'],
            name=site['site_id'],
            line = dict(
        color = ('rgba(22, 22, 22, 0.2)'),
        width = 0.5,)),
            x_col,
            y_col)

# layout = go.Layout(
#     xaxis=dict(domain=[0, 0.45]),
#     yaxis=dict(
#         domain=[0, 0.45],
#         type='log',
#     ),
#     xaxis2=dict(domain=[0.55, 1]),
#     xaxis4=dict(domain=[0.55, 1], anchor='y4'),
#     yaxis3=dict(
#         domain=[0.55, 1],
#         type='log',
#     ),
#     yaxis4=dict(
#         domain=[0.55, 1],
#         anchor='x4',
#         type='log',
#     ))

fig['layout'].update(showlegend=False, title='Specs with Subplot Title',height=800,)

for ax in ['yaxis','yaxis2']:
#     fig['layout'][ax]['type']='log'
    fig['layout'][ax]['range']= [0,100]

for ax in ['xaxis', 'xaxis2']:
    fig['layout'][ax]['range']= [-1,1]

go.FigureWidget(fig)

In [ ]:
fig['layout']['yaxis']